In [27]:
from transformers import pipeline
import json
import pandas as pd
from sklearn.model_selection import train_test_split
from transformers import AlbertTokenizer
from tqdm import tqdm
import re
from datasets import Dataset
from transformers import AutoModelForSequenceClassification
import torch
import numpy as np
from typing import Dict
from transformers import AutoModel
from torch.nn import BCEWithLogitsLoss
from typing import List
from transformers import TrainingArguments, Trainer
from collections import defaultdict

from transformers import __version__ as transformers_version
print(transformers_version)

DEVICE = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
DEVICE

4.48.3


device(type='cuda')

In [2]:
USED_MODEL = "albert-base-v2"

In [3]:
def read_json(json_filename):
    with open(json_filename, 'r') as f:
        return json.loads(f.read())


def save_json(json_object, json_filename, indent=4):
    with open(json_filename, 'w') as f:
        json.dump(json_object, f, separators=(',', ':'), indent=indent)

**Данные берем отсюда: https://www.kaggle.com/datasets/neelshah18/arxivdataset**

In [4]:
arxiv_data = read_json('arxivData.json')

In [5]:
arxiv_data[0]

{'author': "[{'name': 'Ahmed Osman'}, {'name': 'Wojciech Samek'}]",
 'day': 1,
 'id': '1802.00209v1',
 'link': "[{'rel': 'alternate', 'href': 'http://arxiv.org/abs/1802.00209v1', 'type': 'text/html'}, {'rel': 'related', 'href': 'http://arxiv.org/pdf/1802.00209v1', 'type': 'application/pdf', 'title': 'pdf'}]",
 'month': 2,
 'summary': 'We propose an architecture for VQA which utilizes recurrent layers to\ngenerate visual and textual attention. The memory characteristic of the\nproposed recurrent attention units offers a rich joint embedding of visual and\ntextual features and enables the model to reason relations between several\nparts of the image and question. Our single model outperforms the first place\nwinner on the VQA 1.0 dataset, performs within margin to the current\nstate-of-the-art ensemble model. We also experiment with replacing attention\nmechanisms in other state-of-the-art models with our implementation and show\nincreased accuracy. In both cases, our recurrent attention

**Хотим по названию статьи + abstract выдавать наиболее вероятную тематику статьи, скажем, физика, биология или computer science** 

In [6]:
arxiv_topics_df = pd.read_csv('arxiv_topics.csv')
print(len(arxiv_topics_df))
arxiv_topics_df.head(5)

155


tag                                            topic          category
0  cs.AI                          Artificial Intelligence  Computer Science
1  cs.AR                            Hardware Architecture  Computer Science
2  cs.CC                         Computational Complexity  Computer Science
3  cs.CE  Computational Engineering, Finance, and Science  Computer Science
4  cs.CG                           Computational Geometry  Computer Science

In [7]:
category_to_index = {}
tag_to_category = {}
current_index = 0
for i, row in arxiv_topics_df.iterrows():
    category = row['category']
    if category not in category_to_index:
        category_to_index[category] = current_index
        current_index += 1
    tag_to_category[row['tag']] = row['category']
index_to_category = {value: key for key, value in category_to_index.items()}

**Готовим данные к обучению**

In [8]:
def is_valid_tag(tag: str) -> bool:
    return tag in tag_to_category

total_categories_count = 0
total_tags_count = 0
records = []
for arxiv_record in tqdm(arxiv_data):
    record = {
        'title': arxiv_record['title'],
        'summary': arxiv_record['summary'],
        'title_and_summary': arxiv_record['title'] + ' $ ' + arxiv_record['summary'],
        'tags': [current_tag['term'] for current_tag in eval(arxiv_record['tag']) if is_valid_tag(current_tag['term'])]
    }
    categories = set(tag_to_category[tag] for tag in record['tags'])
    total_categories_count += len(categories)
    total_tags_count += len(record['tags'])
    record['categories_indices'] = list(set([category_to_index[tag_to_category[tag]] for tag in record['tags']]))
    assert len(record['tags']) > 0
    records.append(record)

print(f'Среднее число категорий в одной статье: {total_categories_count / len(arxiv_data)}')
print(f'Среднее число тегов в одной статье: {total_tags_count / len(arxiv_data)}')

  0%|          | 0/41000 [00:00<?, ?it/s]

100%|██████████| 41000/41000 [00:01<00:00, 33667.39it/s]

Среднее число категорий в одной статье: 1.3301219512195122
Среднее число тегов в одной статье: 1.8489024390243902


Как видим, перед нами задача мультибинарной классификации.

Тегов у одной статьи бывает много, это понятно, но и категорий тоже бывает много. То есть, условно статья может быть посвящена и физике и биологии одновременно.

Попробуем обучить модель определять теги - так она потенциально может сохранить в себе больше информации, чем если ее обучить определять категории (которых гораздо меньше).

**Соединяем title и summary используя символ `$` - он редкий, при этом его знает токенайзер, поэтому не придется с ним дополнительно возиться**

In [9]:
full_data_df = pd.DataFrame(records)
print(len(full_data_df))
full_data_df.head(5)

41000


title  \
0  Dual Recurrent Attention Units for Visual Ques...   
1  Sequential Short-Text Classification with Recu...   
2  Multiresolution Recurrent Neural Networks: An ...   
3  Learning what to share between loosely related...   
4              A Deep Reinforcement Learning Chatbot   

                                             summary  \
0  We propose an architecture for VQA which utili...   
1  Recent approaches based on artificial neural n...   
2  We introduce the multiresolution recurrent neu...   
3  Multi-task learning is motivated by the observ...   
4  We present MILABOT: a deep reinforcement learn...   

                                   title_and_summary  \
0  Dual Recurrent Attention Units for Visual Ques...   
1  Sequential Short-Text Classification with Recu...   
2  Multiresolution Recurrent Neural Networks: An ...   
3  Learning what to share between loosely related...   
4  A Deep Reinforcement Learning Chatbot $ We pre...   

                                    tags categories_indices  
0  [cs.AI, cs.CL, cs.CV, cs.NE, stat.ML]             [0, 7]  
1  [cs.CL, cs.AI, cs.LG, cs.NE, stat.ML]             [0, 7]  
2  [cs.CL, cs.AI, cs.LG, cs.NE, stat.ML]             [0, 7]  
3  [stat.ML, cs.AI, cs.CL, cs.LG, cs.NE]             [0, 7]  
4  [cs.CL, cs.AI, cs.LG, cs.NE, stat.ML]             [0, 7]

**Как видим, Computer science встречается очень часто. А, например, экономика - совсем редко. Значит при обучении экономике логично давать больше вес**

In [10]:
text_data = list(full_data_df['title_and_summary'])
categories_indices = list(full_data_df['categories_indices'])

In [11]:
X_train_val, X_test, y_train_val, y_test = train_test_split(text_data, categories_indices, test_size=0.1, random_state=42)
X_train, X_val, y_train, y_val = train_test_split(X_train_val, y_train_val, test_size=2/9, random_state=42)
print(len(X_train), len(X_val), len(X_test))
# Train is 70%, val is 20%, test is 10%

28700 8200 4100


Посмотрим на распределение категорий в тренировочной выборке

In [12]:
category_to_count = defaultdict(int)
for row in y_train:
    for category in row:
        category_to_count[category] += 1
category_to_count = dict(category_to_count)
print(category_to_count)

{0: 27475, 3: 1591, 7: 7417, 5: 623, 2: 152, 4: 840, 6: 43, 1: 9}


In [13]:
tokenizer = AlbertTokenizer.from_pretrained(USED_MODEL)
def tokenize_function(text):
    return tokenizer(text, padding="max_length", truncation=True)

In [14]:
train_encodings = tokenize_function(X_train)
val_encodings = tokenize_function(X_val)
test_encodings = tokenize_function(X_test)

print(type(train_encodings))
print(dir(train_encodings))
print(len(train_encodings))

<class 'transformers.tokenization_utils_base.BatchEncoding'>
['_MutableMapping__marker', '__abstractmethods__', '__class__', '__class_getitem__', '__contains__', '__copy__', '__delattr__', '__delitem__', '__dict__', '__dir__', '__doc__', '__eq__', '__format__', '__ge__', '__getattr__', '__getattribute__', '__getitem__', '__getstate__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__ior__', '__iter__', '__le__', '__len__', '__lt__', '__module__', '__ne__', '__new__', '__or__', '__reduce__', '__reduce_ex__', '__repr__', '__reversed__', '__ror__', '__setattr__', '__setitem__', '__setstate__', '__sizeof__', '__slots__', '__str__', '__subclasshook__', '__weakref__', '_abc_impl', '_encodings', '_n_sequences', 'char_to_token', 'char_to_word', 'clear', 'convert_to_tensors', 'copy', 'data', 'encodings', 'fromkeys', 'get', 'is_fast', 'items', 'keys', 'n_sequences', 'pop', 'popitem', 'sequence_ids', 'setdefault', 'to', 'token_to_chars', 'token_to_sequence', 'token_to_word', 'tokens', '

In [15]:
def get_labels(y: List[List[int]]):
  labels = np.zeros((len(y), len(category_to_index)))
  for i in tqdm(range(len(y))):
    labels[i, y[i]] = 1
  return labels.tolist()

labels_train = get_labels(y_train)
labels_val = get_labels(y_val)
labels_test = get_labels(y_test)

100%|██████████| 4100/4100 [00:00<00:00, 516059.37it/s]


In [16]:
train_encodings['labels'] = labels_train
val_encodings['labels'] = labels_val
test_encodings['labels'] = labels_test

**Я использовал пример отсюда чтобы понимать, какой нужен формат данных https://github.com/NielsRogge/Transformers-Tutorials/blob/master/BERT/Fine_tuning_BERT_(and_friends)_for_multi_label_text_classification.ipynb**

In [17]:
train_dataset = Dataset.from_dict(train_encodings)
val_dataset = Dataset.from_dict(val_encodings)
test_dataset = Dataset.from_dict(test_encodings)

train_dataset.set_format("torch")
val_dataset.set_format("torch")
test_dataset.set_format("torch")

In [18]:
model = AutoModelForSequenceClassification.from_pretrained(
    USED_MODEL, 
    problem_type="multi_label_classification", 
    num_labels=len(category_to_index),
    id2label=index_to_category,
    label2id=category_to_index
)

Some weights of AlbertForSequenceClassification were not initialized from the model checkpoint at albert-base-v2 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [19]:
batch_size = 8
metric_name = "f1"

In [20]:
args = TrainingArguments(
    output_dir=f'train-{USED_MODEL}',
    evaluation_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=5,
    weight_decay=0.01,
    load_best_model_at_end=True,
    metric_for_best_model=metric_name,
    push_to_hub=False
)

/home/jarakcyc/.virtualenvs/Tricks/lib/python3.10/site-packages/transformers/training_args.py:1575: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [21]:
from sklearn.metrics import f1_score, roc_auc_score, accuracy_score
from transformers import EvalPrediction
import torch
    
# source: https://jesusleal.io/2021/04/21/Longformer-multilabel-classification/
def multi_label_metrics(predictions, labels, threshold=0.5):
    sigmoid = torch.nn.Sigmoid()
    probs = sigmoid(torch.Tensor(predictions))
    y_pred = np.zeros(probs.shape)
    y_pred[np.where(probs >= threshold)] = 1
    y_true = labels
    f1_micro_average = f1_score(y_true=y_true, y_pred=y_pred, average='micro')
    roc_auc = roc_auc_score(y_true, y_pred, average = 'micro')
    accuracy = accuracy_score(y_true, y_pred)
    metrics = {'f1': f1_micro_average,
               'roc_auc': roc_auc,
               'accuracy': accuracy}
    return metrics

def compute_metrics(p: EvalPrediction):
    preds = p.predictions[0] if isinstance(p.predictions, 
            tuple) else p.predictions
    result = multi_label_metrics(
        predictions=preds, 
        labels=p.label_ids)
    return result

In [22]:
pos_weight=torch.tensor([
    len(y_train) / category_to_count[i] / len(category_to_count) for i in range(len(category_to_count))
]).to(DEVICE)
compute_loss_func_ = BCEWithLogitsLoss(pos_weight=pos_weight)

# Example of custom trainer is taken from https://medium.com/deeplearningmadeeasy/how-to-use-a-custom-loss-with-hugging-face-fc9a1f91b39b
class CustomTrainer(Trainer):
    def compute_loss(self, model, inputs, return_outputs=False, num_items_in_batch=None):
        labels = inputs.pop("labels")
        outputs = model(**inputs)
        logits = outputs.logits
        loss = compute_loss_func_(logits, labels)
        return (loss, outputs) if return_outputs else loss

pos_weight

tensor([1.3057e-01, 3.9861e+02, 2.3602e+01, 2.2549e+00, 4.2708e+00, 5.7584e+00,
        8.3430e+01, 4.8369e-01], device='cuda:0')

In [23]:
trainer = CustomTrainer(
    model,
    args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics
)

/tmp/ipykernel_831875/1711637572.py:1: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `CustomTrainer.__init__`. Use `processing_class` instead.
  trainer = CustomTrainer(


In [24]:
trainer.train()

TrainOutput(global_step=17940, training_loss=0.3050233064819472, metrics={'train_runtime': 3844.3438, 'train_samples_per_second': 37.328, 'train_steps_per_second': 4.667, 'total_flos': 3431411601408000.0, 'train_loss': 0.3050233064819472, 'epoch': 5.0})

In [25]:
trainer.evaluate(eval_dataset=val_dataset)

{'eval_loss': 0.40933170914649963,
 'eval_f1': 0.8577886788823161,
 'eval_roc_auc': 0.8984138467714379,
 'eval_accuracy': 0.7129268292682926,
 'eval_runtime': 69.0762,
 'eval_samples_per_second': 118.71,
 'eval_steps_per_second': 14.839,
 'epoch': 5.0}

In [26]:
trainer.evaluate(eval_dataset=test_dataset)

{'eval_loss': 0.5079951882362366,
 'eval_f1': 0.8536538088776895,
 'eval_roc_auc': 0.8970809313634953,
 'eval_accuracy': 0.708780487804878,
 'eval_runtime': 34.407,
 'eval_samples_per_second': 119.162,
 'eval_steps_per_second': 14.91,
 'epoch': 5.0}

Исходная задача у нас звучала как "хотим увидеть топ-95%* тематик, отсортированных по убыванию вероятности", где под тематиками имелись ввиду категории (физика, биология и так далее)

Будем делать следующее:
- наша модель выдает логиты категорий
- посчитаем с их помощью вероятность категорий, считая их сумму равной 1 (хотя на самом деле категорий может быть несколько)
- выведем требуемые топ-95% тематик

In [29]:
model = AutoModelForSequenceClassification.from_pretrained(
    f"train-{USED_MODEL}/checkpoint-10764", 
    problem_type="multi_label_classification", 
    num_labels=len(category_to_index),
    id2label=index_to_category,
    label2id=category_to_index
).to(DEVICE)

In [30]:
model(**{key: torch.tensor(value).to(model.device).unsqueeze(0) for key, value in tokenize_function('Maths is cool $ In our article we prove that maths is the coolest subject at school').items()})

SequenceClassifierOutput(loss=None, logits=tensor([[ 3.5393, -7.6223, -5.9721, -0.6268, -3.4508, -5.2609, -5.8817, -3.5099]],
       device='cuda:0', grad_fn=<AddmmBackward0>), hidden_states=None, attentions=None)

In [31]:
@torch.no_grad
def get_category_probs_dict(model, title: str, summary: str) -> Dict[str, float]:
    text = f'{title} $ {summary}'
    category_logits = model(**{key: torch.tensor(value).to(model.device).unsqueeze(0) for key, value in tokenize_function(text).items()}).logits
    sigmoid = torch.nn.Sigmoid()
    category_probs = sigmoid(category_logits.squeeze().cpu()).numpy()
    category_probs /= category_probs.sum()
    category_probs_dict = {category: 0.0 for category in set(arxiv_topics_df['category'])}
    for index in range(len(index_to_category)):
        category_probs_dict[index_to_category[index]] += float(category_probs[index])
    return category_probs_dict

In [33]:
def get_most_probable_keys(probs_dict: Dict[str, float], target_probability: float, print_probabilities: bool) -> List[str]:
    current_p = 0
    probs_list = sorted([(value, key) for key, value in probs_dict.items()])[::-1]
    current_index = 0
    answer = []
    while current_p <= target_probability:
        current_p += probs_list[current_index][0]
        if not print_probabilities:
            answer.append(probs_list[current_index][1])
        else:
            answer.append(f'{probs_list[current_index][1]} ({probs_list[current_index][0]})')
        current_index += 1
        if current_index >= len(probs_list):
            break
    return answer

Сохраняем модель, чтобы потом можно было её использовать в huggingface space

In [35]:
model.push_to_hub(f"bumchik2/train-{USED_MODEL}-tags-classification")

model.safetensors: 100%|██████████| 46.8M/46.8M [00:06<00:00, 7.25MB/s]  


CommitInfo(commit_url='https://huggingface.co/bumchik2/train-albert-base-v2-tags-classification/commit/bf0db75a370cbbfeed52bcb5760c9adfea198bf9', commit_message='Upload AlbertForSequenceClassification', commit_description='', oid='bf0db75a370cbbfeed52bcb5760c9adfea198bf9', pr_url=None, repo_url=RepoUrl('https://huggingface.co/bumchik2/train-albert-base-v2-tags-classification', endpoint='https://huggingface.co', repo_type='model', repo_id='bumchik2/train-albert-base-v2-tags-classification'), pr_revision=None, pr_num=None)

Теперь я могу загружать свою модель оттуда

In [36]:
model = AutoModelForSequenceClassification.from_pretrained(
    f"bumchik2/train-{USED_MODEL}-tags-classification", 
    problem_type="multi_label_classification", 
    num_labels=len(category_to_index),
    id2label=index_to_category,
    label2id=category_to_index
).to(DEVICE)

Протестируем на нескольких реальных примерах:

In [39]:
# правильный ответ Quantitative Biology
get_most_probable_keys(
    probs_dict=get_category_probs_dict(
        model=model,
        title='Simulating cell populations with explicit cell cycle length -- implications to cell cycle dependent tumour therapy',
        summary='In this study, we present a stochastic simulation model designed to explicitly incorporate cell cycle length, overcoming limitations associated with classical compartmental models. Our approach employs a delay mechanism to represent the cell cycle, allowing the use of arbitrary distributions for cell cycle lengths. We demonstrate the feasibility of our model by fitting it to experimental data from melanoma cell lines previously studied by Vittadello et al. Notably, our model successfully replicates experimentally observed synchronization phenomena that multi-stage models could not adequately explain. By using a gamma distribution to model cell cycle lengths, we achieved excellent agreement between our simulations and empirical data, while significantly reducing computational complexity and parameter estimation challenges inherent in multi-stage approaches. Our results highlight the importance of explicitly incorporating cell cycle lengths in modeling cell populations, with potential implications for optimizing cell cycle-dependent tumor therapies.'
    ),
    target_probability=0.95,
    print_probabilities=True
)

['Quantitative Biology (0.4282848834991455)',
 'Statistics (0.34262675046920776)',
 'Computer Science (0.14248277246952057)',
 'Physics (0.034869205206632614)',
 'Mathematics (0.029306704178452492)']

In [40]:
# правильный ответ Physics
get_most_probable_keys(
    probs_dict=get_category_probs_dict(
        model=model,
        title='Performance Improvement of LTS Undulators for Synchrotron Light Sources',
        summary='The joint expertise of ANL and FNAL has led to the production of Nb3Sn undulator magnets in operation in the ANL Advanced Photon Source (APS). These magnets showed performance reproducibility close to the short sample limit, and a design field increase of 20% at 820A. However, the long training did not allow obtaining the expected 50% increase of the on-axis magnetic field with respect to the ~1 T produced at 450 A current in the ANL NbTi undulator. To address this, 10-pole long undulator prototypes were fabricated, and CTD-101K was replaced as impregnation material with TELENE, an organic olefin-based thermosetting dicyclopentadiene resin produced by RIMTEC Corporation, Japan. Training and magnet retraining after a thermal cycle were nearly eliminated, with only a couple of quenches needed before reaching short sample limit at over 1,100 A. TELENE will enable operation of Nb3Sn undulators much closer to their short sample limit, expanding the energy range and brightness intensity of light sources. TELENE is Co-60 gamma radiation resistant up to 7-8 MGy, and therefore already applicable to impregnate planar, helical and universal devices operating in lower radiation environments than high energy colliders.'
    ),
    target_probability=0.95,
    print_probabilities=True
)

['Computer Science (0.48184847831726074)',
 'Physics (0.41395917534828186)',
 'Statistics (0.029943009838461876)',
 'Electrical Engineering and Systems Science (0.028027774766087532)']